### LIBRARY IMPORT

In [20]:
import numpy as np
import pandas as pd
pd.set_option('display.max_columns', None)
# pd.set_option('display.max_rows', None)
from contextlib import contextmanager
import time  
from sklearn.neighbors import NearestNeighbors  
from sklearn.preprocessing import minmax_scale  
from typing import Dict, List, Optional, Tuple  
import seaborn as sns 
import gc
import traceback 

import matplotlib.pyplot as plt

from scipy.stats import kendalltau

import os
# os.environ["MODIN_ENGINE"] = "dask"  # Modin will use Dask
working_directory = 'D:\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'  ## 서로 다른 환경에서는 이곳을 수정해야 함.
# working_directory = 'C:\\Users\\user\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'

os.chdir(working_directory)
gc.collect()

vn=3

### Drop Early morning period & CHECK NULL VALUE

In [36]:
# combined_result_df = pd.read_csv("./DB/professor_BTC_sum_both_10m.csv")
combined_result_df_raw = pd.read_csv("./output/BTC_sum_both_10m_{}.csv".format(vn))
print("# of rows of combined_Result_Df:", combined_result_df_raw.shape[0])

combined_result_df_raw['window_start'] = pd.to_datetime(combined_result_df_raw['window_start'])  # Convert to datetime

# Define the time range
start_time = pd.to_datetime('00:00:00').time()
end_time = pd.to_datetime('06:00:00').time()

# 10분간 return 추가
combined_result_df_raw['return'] = np.log(combined_result_df_raw['end_price'].shift(-10) / combined_result_df_raw['end_price'])

# Filter and drop rows (새벽시간 삭제하기)
filtered_df = combined_result_df_raw[~combined_result_df_raw['window_start'].apply(lambda x: start_time <= x.time() <= end_time)]
print("# of rows of filtered_df:", filtered_df.shape[0])

# Set the target variable:
target_var = 'dv5_realized_volatility_mean0'
target_var_3 = target_var[:3]
print("target_var_3:", target_var_3)

# 사용하지 않을 변수(column)들 미리 제거 (dropna 효과를 최소화하기 위해.)
remove_varlist0 = [
                  'window_start', 
                  'window_end',
                  'prices_30s_for_NN',
                  'window_end_150_ticker',
                  'window_end_300_ticker',
                  'window_end_450_ticker',
                  'window_end_150_orderbook',
                  'window_end_300_orderbook',
                  'window_end_450_orderbook',

                  # 'volume_power',
                  # 'volume_power_150',
                  # 'volume_power_300',
                  # 'volume_power_450',
                  
                  'end_price',
                  'realized_volatility_30s',

                #   'dv1_realized_volatility',
                  'dv2_lowest_return',
                  'dv3_highest_return',
                  'dv4_realized_volatility_30s',
                  'dv5_realized_volatility_mean0',

                  # 'prices_30s_for_NN_onlyprices',
                  ]
remove_varlist0.remove(target_var)

# 이 두 아래의 변수도 NN feature를 뽑을 때에는 활용해보자.
remove_varlist0.remove('dv2_lowest_return')
remove_varlist0.remove('dv3_highest_return')

main_feature_list = list(filtered_df.columns)

for i in range(len(remove_varlist0)):
    # print(remove_varlist0[i])
    main_feature_list.remove(remove_varlist0[i])

## 제거하기 전에, 30초 주가 데이터를 따로 저장.
# listed_time_series_df = filtered_df['only_prices_30s_for_NN'].copy()
# combined_result_df = combined_result_df.drop('prices_30s_for_NN_onlyprices', axis=1)

filtered_df = filtered_df[main_feature_list]

combined_result_df = filtered_df.dropna()

combined_result_df['volume_power'] = combined_result_df['volume_power'] / combined_result_df['trade_vol']
combined_result_df['volume_power_150'] = combined_result_df['volume_power_150'] / combined_result_df['trade_vol_150']
combined_result_df['volume_power_300'] = combined_result_df['volume_power_300'] / combined_result_df['trade_vol_300']
combined_result_df['volume_power_450'] = combined_result_df['volume_power_450'] / combined_result_df['trade_vol_450']

combined_result_df = combined_result_df[~combined_result_df.isin([np.inf, -np.inf]).any(axis=1)]
combined_result_df = combined_result_df.reset_index(drop=True)

print("# of rows of filtered_df:", combined_result_df.shape[0])

# 평균이 아닌 이전 값으로 Null 채우기
# combined_result_df = combined_result_df.fillna(method='ffill') 

# # Temporary take the first N rows
# take_first_rows = 30000
# combined_result_df = combined_result_df.head(take_first_rows)

# 오히려 초반 10000개를 떼어내고 분석하면?
# combined_result_df = combined_result_df.iloc[7000:]

print("combined_result_df.dtypes:", combined_result_df.dtypes)
print("combined_result_df.shape:", combined_result_df.shape)
combined_result_df.head(3)

gc.collect()

# of rows of combined_Result_Df: 102336
# of rows of filtered_df: 76766
target_var_3: dv5


c:\Users\hhkim\AppData\Local\Programs\Python\Python37\lib\site-packages\ipykernel_launcher.py:71: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
c:\Users\hhkim\AppData\Local\Programs\Python\Python37\lib\site-packages\ipykernel_launcher.py:72: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
c:\Users\hhkim\AppData\Local\Programs\Python\Python37\lib\site-packages\ipykernel_launcher.py:73: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer

# of rows of filtered_df: 72151
combined_result_df.dtypes: realized_volatility_mean0         float64
realized_up_volatility_mean0      float64
realized_down_volatility_mean0    float64
num_trades                          int64
lowest_return                     float64
                                   ...   
tvpl_ep1                          float64
tvpl_ep2                          float64
tvpl_ep5                          float64
tvpl_ep10                         float64
tvpl_ep15                         float64
Length: 98, dtype: object
combined_result_df.shape: (72151, 98)


0

In [37]:
import re
def extract_floats_from_series(df):
    def extract_floats(s):
        return [float(num) for num in re.findall(r"(-?\d+\.\d+)", s)]

    df['only_prices_30s_for_NN'] = df['prices_30s_for_NN_onlyprices'].apply(extract_floats)
    
    # 데이터 포인트가 20개가 아닌 행을 삭제
    mask = df['only_prices_30s_for_NN'].apply(len) == 20
    df = df[mask].reset_index(drop=True)
    
    return df

In [38]:
combined_result_df.head(3)

realized_volatility_mean0  realized_up_volatility_mean0  \
0                   0.000105                      0.000084   
1                   0.000107                      0.000086   
2                   0.000106                      0.000085   

   realized_down_volatility_mean0  num_trades  lowest_return  highest_return  \
0                        0.000187         376      -0.000089        0.001815   
1                        0.000185         361      -0.000089        0.001815   
2                        0.000189         365       0.000000        0.001815   

   high_low_gap  trade_vol  volume_power    return              time_id  \
0      0.001904  13.756273      0.181296  0.001150  2022-12-16 21:44:00   
1      0.001904  12.615168      0.116172  0.000664  2022-12-16 21:45:00   
2      0.001815  13.313910      0.122327  0.000442  2022-12-16 21:46:00   

   BB_width_w20  BB_width_w40  BB_width_w10  dv5_realized_volatility_mean0  \
0  48144.956559  47257.071103  55194.202594                       0.000154   
1  50564.809898  50311.440306  54273.382058                       0.000156   
2  53873.536126  53013.302636  51861.353627                       0.000159   

   dv2_lowest_return  dv3_highest_return  realized_volatility_mean0_150  \
0          -0.000310            0.001238                       0.000046   
1          -0.000177            0.001371                       0.000077   
2          -0.000044            0.001238                       0.000140   

   num_trades_150  lowest_return_150  highest_return_150  high_low_gap_150  \
0              85          -0.000089            0.000089          0.000177   
1              68          -0.000089            0.000354          0.000443   
2              69           0.000000            0.000354          0.000354   

   trade_vol_150  volume_power_150  realized_volatility_mean0_300  \
0       3.814411          0.184372                       0.000100   
1       1.921894          0.632472                       0.000106   
2       2.159312          0.429273                       0.000109   

   num_trades_300  lowest_return_300  highest_return_300  high_low_gap_300  \
0             147          -0.000089            0.000354          0.000443   
1             126          -0.000089            0.000399          0.000487   
2             125           0.000000            0.000753          0.000753   

   trade_vol_300  volume_power_300  realized_volatility_mean0_450  \
0       5.543539          0.264701                       0.000092   
1       3.760741          0.564018                       0.000116   
2       4.498119          0.712681                       0.000119   

   num_trades_450  lowest_return_450  highest_return_450  high_low_gap_450  \
0             209          -0.000089            0.001284          0.001373   
1             259          -0.000089            0.001815          0.001904   
2             286           0.000000            0.001815          0.001815   

   trade_vol_450  volume_power_450  liq_last_1  liq_last_2  liq_last_5  \
0       9.178568          0.538060    0.003128    0.003207    0.003479   
1       9.098996          0.388909    0.001284    0.001624    0.002042   
2       9.661851          0.297913    0.001621    0.001628    0.002304   

   liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  ep_liq_5  ep_liq_10  \
0     0.003642     0.003871  0.000475  0.000668  0.001029   0.001296   
1     0.002314     0.002419  0.000472  0.000647  0.000948   0.001205   
2     0.002582     0.002729  0.000488  0.000659  0.000952   0.001197   

   ep_liq_15  bidask_spread_0  bidask_spread_1  liq_last_1_150  \
0   0.001752         2.030769        10.261539        0.001555   
1   0.001527         2.098361        13.000000        0.000299   
2   0.001454         1.487500         9.412500        0.000284   

   liq_last_2_150  liq_last_5_150  liq_last_10_150  liq_last_15_150  \
0        0.001704        0.002171         0.002716         0.003100   
1        0.000458        0.00070

In [39]:
combined_result_df = extract_floats_from_series(combined_result_df)
combined_result_df.reset_index(drop=True, inplace=True)
print("combined_result_df.shape (After dropping windows without 20 prices):", combined_result_df.shape)
listed_time_series_df = combined_result_df['only_prices_30s_for_NN'].copy()
combined_result_df = combined_result_df.drop('prices_30s_for_NN_onlyprices', axis=1)
combined_result_df = combined_result_df.drop('only_prices_30s_for_NN', axis=1)

gc.collect()

combined_result_df.shape (After dropping windows without 20 prices): (72151, 99)


0

In [40]:
float64_features = combined_result_df.select_dtypes(include=['float64']).columns.tolist()
int64_features = combined_result_df.select_dtypes(include=['int64']).columns.tolist()

combined_result_df[float64_features] = combined_result_df[float64_features].astype('float32')
combined_result_df[int64_features] = combined_result_df[int64_features].astype('int32')

gc.collect()

0

In [41]:
print("combined_result_df.dtypes:", combined_result_df.dtypes)

combined_result_df.dtypes: realized_volatility_mean0         float32
realized_up_volatility_mean0      float32
realized_down_volatility_mean0    float32
num_trades                          int32
lowest_return                     float32
                                   ...   
tvpl_ep1                          float32
tvpl_ep2                          float32
tvpl_ep5                          float32
tvpl_ep10                         float32
tvpl_ep15                         float32
Length: 97, dtype: object


### Manipulating Features => Log transformation of some liquidity measures (Why?)

In [42]:
# combined_result_df['liq_last_1'] = np.log10(combined_result_df['liq_last_1'] + 0.00001)
# combined_result_df['liq_last_2'] = np.log10(combined_result_df['liq_last_2'] + 0.00001)
# combined_result_df['liq_last_5'] = np.log10(combined_result_df['liq_last_5'] + 0.00001)
# combined_result_df['liq_last_10'] = np.log10(combined_result_df['liq_last_10'] + 0.00001)
# combined_result_df['liq_last_15'] = np.log10(combined_result_df['liq_last_15'] + 0.00001)
# combined_result_df['trade_vol'] = np.log10(combined_result_df['trade_vol'] + 0.00001)
# combined_result_df['num_trades'] = np.log10(combined_result_df['num_trades'] + 0.00001)

In [54]:
data = combined_result_df
correlation_matrix = data.corr(method=lambda x, y: kendalltau(x, y).correlation)
correlation_matrix_series = correlation_matrix[target_var].copy() # .sort_values(ascending=False)
correlation_matrix_series.sort_values(ascending=False, inplace=True)

correlation_matrix_series
gc.collect()

20

In [88]:
N_of_features_for_finding_NN = 35 ## dv5 와 가장 관련성이 높은 20개 변수를 꼽아서 nn에 활용하자.

feature_list_for_finding_NN = correlation_matrix_series.index[1:1+N_of_features_for_finding_NN]

string_to_remove = ["dv2_lowest_return", 'dv3_highest_return']

# Create a new list without the specified string
for i in range(len(string_to_remove)):
    new_list = [item for item in feature_list_for_finding_NN if item != string_to_remove[i]]

# new_list will contain elements from my_list except for "banana"
print(new_list)

feature_list_for_finding_NN = new_list

gc.collect()

['bidask_spread_1', 'realized_up_volatility_mean0', 'realized_volatility_mean0', 'realized_down_volatility_mean0', 'bidask_spread_0', 'realized_volatility_mean0_450', 'realized_volatility_mean0_300', 'bidask_spread_1_450', 'tvpl_ep1', 'tvpl_ep2', 'tvpl2', 'tvpl5', 'tvpl_ep5', 'bidask_spread_1_300', 'tvpl1', 'bidask_spread_0_450', 'tvpl10', 'high_low_gap', 'realized_volatility_mean0_150', 'tvpl15', 'tvpl_ep10', 'bidask_spread_0_300', 'high_low_gap_450', 'high_low_gap_300', 'bidask_spread_1_150', 'tvpl_ep15', 'BB_width_w10', 'high_low_gap_150', 'bidask_spread_0_150', 'BB_width_w20', 'highest_return', 'highest_return_450', 'highest_return_300', 'highest_return_150']


42

In [89]:
print(len(feature_list_for_finding_NN))
feature_list_for_finding_NN

34


['bidask_spread_1',
 'realized_up_volatility_mean0',
 'realized_volatility_mean0',
 'realized_down_volatility_mean0',
 'bidask_spread_0',
 'realized_volatility_mean0_450',
 'realized_volatility_mean0_300',
 'bidask_spread_1_450',
 'tvpl_ep1',
 'tvpl_ep2',
 'tvpl2',
 'tvpl5',
 'tvpl_ep5',
 'bidask_spread_1_300',
 'tvpl1',
 'bidask_spread_0_450',
 'tvpl10',
 'high_low_gap',
 'realized_volatility_mean0_150',
 'tvpl15',
 'tvpl_ep10',
 'bidask_spread_0_300',
 'high_low_gap_450',
 'high_low_gap_300',
 'bidask_spread_1_150',
 'tvpl_ep15',
 'BB_width_w10',
 'high_low_gap_150',
 'bidask_spread_0_150',
 'BB_width_w20',
 'highest_return',
 'highest_return_450',
 'highest_return_300',
 'highest_return_150']

### NUMERIC FEATURES & CALCULATE CORR 

In [90]:
# ## 이웃을 찾는 기준이 되는 변수들.

# feature_list_for_finding_NN = []
# feature_list_for_finding_NN.append('realized_volatility_mean0')
# feature_list_for_finding_NN.append('bidask_spread_0')
# feature_list_for_finding_NN.append('bidask_spread_1')
# feature_list_for_finding_NN.append('highest_return')
# feature_list_for_finding_NN.append('lowest_return')
# feature_list_for_finding_NN.append('num_trades')
# feature_list_for_finding_NN.append('high_low_gap')
# feature_list_for_finding_NN.append('BB_width_w10')
# feature_list_for_finding_NN.append('BB_width_w20')
# feature_list_for_finding_NN.append('BB_width_w40')
# feature_list_for_finding_NN.append('liq_last_1')
# feature_list_for_finding_NN.append('liq_last_2')
# feature_list_for_finding_NN.append('liq_last_5')
# feature_list_for_finding_NN.append('ep_liq_1')
# feature_list_for_finding_NN.append('ep_liq_2')
# feature_list_for_finding_NN.append('ep_liq_5')
# feature_list_for_finding_NN.append('tvpl1')
# feature_list_for_finding_NN.append('tvpl2')
# feature_list_for_finding_NN.append('tvpl5')
# feature_list_for_finding_NN.append('tvpl_ep1')
# feature_list_for_finding_NN.append('tvpl_ep2')
# feature_list_for_finding_NN.append('tvpl_ep5')
# feature_list_for_finding_NN.append('trade_vol')
# feature_list_for_finding_NN.append('trade.tau')
# feature_list_for_finding_NN.append('return')

# feature_list_for_finding_NN.append('volume_power')


In [91]:
# # main_feature_list = list(combined_result_df.columns)
# # feature_list_for_finding_NN.append(target_var)


# # feature_list_for_corr = list(combined_result_df.columns)

# # remove_varlist = [
# #                   'time_id'
# #                   ]

# # for i in range(len(remove_varlist)):
# #     # print(remove_varlist[i])
# #     feature_list_for_corr.remove(remove_varlist[i])


# gc.collect()

In [92]:
# data = combined_result_df
# correlation_matrix = data[feature_list_for_finding_NN].corr(method=lambda x, y: kendalltau(x, y).correlation)

# feature_list_for_finding_NN.remove(target_var)

# correlation_matrix_series = correlation_matrix[target_var].copy() # .sort_values(ascending=False)
# correlation_matrix_series.sort_values(ascending=False, inplace=True)

# gc.collect()

In [93]:
# correlation_matrix_series

In [94]:
combined_result_df_mfl = combined_result_df
combined_result_df_mfl.shape

(72151, 97)

In [95]:
import re
from joblib import Parallel, delayed
from numba import jit

# Numba를 사용하여 최적화된 Hausdorff 거리 계산 함수
@jit(nopython=True)
def compute_hausdorff_modified_numba(x, y):
    min_distances = np.abs(np.subtract(x, y))
    return np.max(min_distances)

# 주어진 시계열 대상과 다른 모든 시계열 간의 거리를 계산하는 함수
def compute_distances(target_series, series_list):
    return [compute_hausdorff_modified_numba(target_series, s) for s in series_list]

# 병렬 처리를 사용하여 특정 시계열과 가장 유사한 시계열의 인덱스를 찾는 함수
def parallel_similarity(df, idx, num_similar, window_size ):
    if idx < window_size :
        return np.array([0] * num_similar)
    
    target_series = np.array(df.iloc[idx])
    
    other_series = []
    
    for series in df.iloc[idx-window_size:idx] :
        other_series.append(np.array(series))
            
    distances = compute_distances(target_series, other_series)
    similar_indices = list(np.argsort(distances)[:num_similar])
    
    similar_indices = [(idx - window_size + x) for x in similar_indices]
    
    return similar_indices

# 병렬 처리를 사용하여 모든 시계열 간의 유사도를 계산하는 함수
def compute_similarity_parallel(df, num_similar=10, window_size = 10000):
    # 빈 2D 배열 생성
    results = np.array([]).reshape(0, num_similar)  # 2D 배열, 0행 2열
    
    for idx in range(len(df)):
        # if (idx + 1) % (len(df) // 10) == 0:
        #     print(f"Processed {idx + 1} rows ({((idx + 1) / len(df)) * 100:.1f}%)")
        result = parallel_similarity(df, idx, num_similar, window_size)
        results = np.append(results, [result], axis=0)
        
    return results

### BUILD NEIGHBORS

In [96]:
N_NEIGHBORS_MAX = 64        
WINDOW_SIZE = 20000

class Neighbors:
    def __init__(self, 
                 name: str, 
                 pivot: pd.DataFrame, 
                 p: float, 
                 metric: str = 'minkowski', 
                 metric_params: object = None, 
                 exclude_self: bool = True,
                 haus_metric = False,
                 ):
        self.name = name
        self.exclude_self = exclude_self
        self.p = p
        self.metric = metric
        self.neighbors = np.empty((0, N_NEIGHBORS_MAX), dtype=int)  # 빈 2D 배열로 초기화

        nn = NearestNeighbors(
            n_neighbors=N_NEIGHBORS_MAX, 
            p=p, 
            metric=metric, 
            metric_params=metric_params
        )
        
        # nn.fit(pivot)
        # _, self.neighbors = nn.kneighbors(pivot, return_distance=True)

        # 이웃을 찾을 이전 window 벙뮈
        window_size = WINDOW_SIZE

        if haus_metric == True : 
            # print("Checkpoint-haus_metric-BEGIN")

            self.neighbors = compute_similarity_parallel(listed_time_series_df, num_similar=N_NEIGHBORS_MAX, window_size = WINDOW_SIZE)
            self.neighbors = self.neighbors.astype(int)
            # print("Checkpoint-haus_metric-END")

        else:
            col_names = pivot.columns
            index_name = pivot.index.name
            
            for t in range(len(pivot)) :
                if t % 1000 == 0:
                    print("name: {}, iteration: {}".format(self.name, t))
                # window size 까지의 데이터는 random NN 설정
                # 1 ~ window 범위의 데이터는 추후 버려야 함
                if t < window_size :
                    update_array = np.random.permutation(np.arange(1, N_NEIGHBORS_MAX+1))
                    self.neighbors = np.append(self.neighbors, [update_array], axis = 0)
                    
                else :
                    # print("Checkpoint#1")

                    # pvdf = pd.DataFrame(pivot.iloc[t-window_size:t])
                    pvdf = pivot.iloc[t-window_size:t].values
                    # print("Checkpoint#1-1-0, pvdf.head(1):", pvdf.head(1))

                    # print("Checkpoint#1-1-1, list(col_names):", list(col_names))
                    # print("Checkpoint#1-1-2, type([list(col_names)]):", type([list(col_names)]))

                    # # col_names = list(col_names)
                    # # pvdf.columns = col_names
                    # print("Checkpoint#1-2")
                    # print("Checkpoint#1-2-1, //after// pvdf.columns:", pvdf.columns)

                    # pvdf.columns = list(col_names)
                    # pvdf = pvdf.rename_axis(index_name)
                    # print("Checkpoint#1-3")

                    nn.fit(pvdf)
                  
                    # print("Checkpoint#2")
                    update_array = nn.kneighbors(pivot.iloc[t].values.reshape(1,-1), n_neighbors=N_NEIGHBORS_MAX , return_distance=False)
                                      
                    # print("Checkpoint#3, update_array:", update_array)

                    update_array = update_array.reshape(-1) + (t-window_size)
                    # print("Checkpoint#4")

#                     print("self.neighbors.shape", self.neighbors.shape)
#                     print("update_array.shape", update_array.shape)

                    # self.neighbors = np.append(self.neighbors, update_array, axis = 0)
                    self.neighbors = np.vstack((self.neighbors, update_array))
#                     print("NEWLY UPDATED self.neighbors.shape", self.neighbors.shape)

                    # print("Checkpoint#5")

                    # if t // 10000 == 0 :
                    #    print(t,self.neighbors)
                    gc.collect()


        self.columns = self.index = self.feature_values = self.feature_col = None

    def rearrange_feature_values(self, df: pd.DataFrame, feature_col: str) -> None:
        raise NotImplementedError()

    def make_nn_feature(self, n=5, agg=np.mean) -> pd.DataFrame:
        assert self.feature_values is not None, "should call rearrange_feature_values beforehand"

        start = 0 if self.exclude_self else 0 # 이미 window 내에 자기자신이 없으므로 start= 0 이어도 된다.

        pivot_aggs = pd.DataFrame(
            agg(self.feature_values[start:n+start,:,0], axis=0), 
            columns=self.columns, 
            index=self.index[WINDOW_SIZE:]
        )

        dst = pivot_aggs.reset_index() # unstack().
        # print("dst.shape:", dst.shape)
        new_column_names = ['time_id', f'{self.feature_col}_nn{n}_{self.name}_{agg.__name__}'] # 3개를 예측했는데 2개만 들어왔다??
        dst.columns = new_column_names 
        return dst
    

class TimeIdNeighbors(Neighbors):
    def rearrange_feature_values(self, df: pd.DataFrame, feature_col: str, data_df: pd.DataFrame) -> None:
        # feature_pivot = df.pivot(index='time_id', values=feature_col)
        # feature_pivot = feature_pivot.fillna(feature_pivot.mean())

        # print('CHEKCPOINT#1')
        feature_df = data_df[['time_id', feature_col]]
        # print('CHEKCPOINT#2')

        # 첫 WINDOW_SIZE 만큼은 랜덤하게 부여된 이웃이므로 제거.
        # feature_df = feature_df.drop(range(WINDOW_SIZE))

        feature_df.set_index('time_id', inplace=True)
        # feature_df = feature_df.fillna(feature_df.mean())

        feature_values = np.zeros((N_NEIGHBORS_MAX, df.shape[0], 1))
        temp_neighbors = self.neighbors[WINDOW_SIZE:,:]
 
        # print("feature_values", feature_values.shape)
        # print("feature_df", feature_df.shape)
        # print("self.neighbors.shape", self.neighbors.shape)
        # print("temp_neighbors", temp_neighbors.shape)

        for i in range(N_NEIGHBORS_MAX):
            # feature_values[i, :, 0] += feature_df.values[self.neighbors[:, i], 0]
            feature_values[i, :, 0] += feature_df.values[temp_neighbors[:, i], 0]

        self.columns = list(feature_df.columns)
        self.index = list(feature_df.index)
        self.feature_values = feature_values
        self.feature_col = feature_col

    def __repr__(self) -> str:
        return f"time-id NN (name={self.name}, metric={self.metric}, p={self.p})"


### PROGRESS CHECK FUNCTION

In [97]:
@contextmanager
def timer(name: str):
    s = time.time()
    yield
    elapsed = time.time() - s
    print(f'[{name}] {elapsed: .3f}초')

def print_trace(name: str = ''):
    print(f'{name or "익명"}에서 에러가 발생했습니다.')
    print(traceback.format_exc())


### GET NN CLASS. Output: {}_sum_plus_nn_features.csv

In [98]:
from sklearn.preprocessing import StandardScaler
from itertools import combinations

# StandardScaler 객체 생성
scaler = StandardScaler()

USE_ONE_FEATURE_C = False
USE_ONE_FEATURE_M_1 = True
USE_ONE_FEATURE_M_2 = False

USE_TWO_FEATURES = True
USE_TWO_FEATURES_ALL_COMB = False
USE_SEVALRAL_FEATURES = True
USE_ALL_FEATURES = True

USE_HAUSDORFF_FEATURES = True

# Top 5 Related Feature
top_5_high_feat = list(correlation_matrix_series.keys())[1:6]
top_5_low_feat = list(correlation_matrix_series.keys())[-5:]

# Top 5 Absolute Related Feature
sorted_data = correlation_matrix_series.abs().sort_values(ascending=False)
top_5_high_abs_feat = list(sorted_data.head(6).keys())[1:]
top_5_low_abs_feat = list(sorted_data.tail(5).keys())

# time_id_neighbors List 
time_id_neighbors: List[Neighbors] = []

with timer('knn fit'):
    df_pv = combined_result_df_mfl.copy()
    # df_pv = df_pv.drop(['window_start', 'window_end','volume_power'], axis=1)
    
    # Standard All Feature
    # df_pv[feature_list_for_finding_NN] = scaler.fit_transform(df_pv[feature_list_for_finding_NN])

    feature_list = list(df_pv.columns)
    feature_list.remove('time_id') # Can't be standardized
    # feature_list.remove('only_prices_30s_for_NN')
    # feature_list.remove('prices_30s_for_NN_onlyprices') # Can't be standardized
    # feature_list.remove('time_id')
    df_pv[feature_list] = scaler.fit_transform(df_pv[feature_list])
    # combined_result_df_mfl_scaled.head(3)



    #### USE ONLY ONE FACTOR ####

    # ## Canberra Distance
    if USE_ONE_FEATURE_C :
        print("ONE FACTOR: Canberra Distance")
        for feat in feature_list_for_finding_NN :
            gc.collect()
            df_nn = df_pv[['time_id',feat]]
            df_nn.set_index('time_id', inplace=True)
            # df_nn = df_nn.fillna(df_nn.mean())

            time_id_neighbors.append(
                TimeIdNeighbors(
                    feat + '_c', 
                    df_nn, 
                    p=2, 
                    metric='canberra', 
                    exclude_self=True
                )
            )
            
    ## Manhattan Distance
    
    if USE_ONE_FEATURE_M_1:
        print("ONE FACTOR: Manhattan Distance")

        for feat in feature_list_for_finding_NN :
            gc.collect()
            df_nn = df_pv[['time_id',feat]]
            df_nn.set_index('time_id', inplace=True)
            # df_nn = df_nn.fillna(df_nn.mean())

            time_id_neighbors.append(
                TimeIdNeighbors(feat + '_m_p1', df_nn, p=1, exclude_self=True)
            )

    # ## Euclidean Distance
    if USE_ONE_FEATURE_M_2:
        print("ONE FACTOR: Euclidean Distance")

        for feat in feature_list_for_finding_NN :
            gc.collect()
            df_nn = df_pv[['time_id',feat]]
            df_nn.set_index('time_id', inplace=True)
            # df_nn = df_nn.fillna(df_nn.mean())

            time_id_neighbors.append(
                TimeIdNeighbors(feat + '_m_p2', df_nn, p=2, exclude_self=True)
            )


    # #### TWO FACTOR ####

    if USE_TWO_FEATURES:
        feature_list = ['time_id','realized_volatility_mean0','bidask_spread_0'] # target variable이 바뀌면 2번/3번 변수 수정해주어야.
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        df_nn = df_nn.fillna(df_nn.mean())

        # ## Canberra

        # time_id_neighbors.append(
        #         TimeIdNeighbors(
        #             'two_c',  # before correction: feat + 'two_c', 
        #             df_nn, 
        #             p=2, 
        #             metric='canberra', 
        #             exclude_self=True
        #         )
        #     )
        ## Euclidean Distance
        time_id_neighbors.append(
            TimeIdNeighbors(
                'two_m', 
                df_nn, 
                p=2, 
                exclude_self=True
            )
        )


    if USE_TWO_FEATURES_ALL_COMB:
        print("TWO FACTORS: all possible combinations")

        combinations_list = list(combinations(feature_list_for_finding_NN, 2))

        for feat in combinations_list :
            gc.collect()
            # feature_list_for_finding_NN
            # combinations_list = list(combinations(feature_list_for_finding_NN, 2))

            feature_list = ['time_id',feat[0],feat[1]] # target variable이 바뀌면 2번/3번 변수 수정해주어야.
            df_nn = df_pv[feature_list]
            df_nn.set_index('time_id', inplace=True)
            # df_nn = df_nn.fillna(df_nn.mean())

            ## Canberra

            # time_id_neighbors.append(
            #         TimeIdNeighbors(
            #             'two_c',  # before correction: feat + 'two_c', 
            #             df_nn, 
            #             p=2, 
            #             metric='canberra', 
            #             exclude_self=True
            #         )
            #     )
            ## Euclidean Distance
            time_id_neighbors.append(
                TimeIdNeighbors(
                    'two_comb_{}_{}_m'.format(feat[0],feat[1]), 
                    df_nn, 
                    p=2, 
                    exclude_self=True
                )
            )



    #### USE SEVALRAL FACTOR ####

    if USE_SEVALRAL_FEATURES:
        print("FIVE FACTORS")

        ## High Related Feature 
        feature_list = ['time_id']
        feature_list += top_5_high_feat
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        # df_nn = df_nn.fillna(df_nn.mean())

        ### Euclidean Distance
        time_id_neighbors.append(
            TimeIdNeighbors(
                'high5_nn_m', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )

        ## Low Related Feature

        feature_list = ['time_id']
        feature_list += top_5_low_feat
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        # df_nn = df_nn.fillna(df_nn.mean())        

        time_id_neighbors.append(
            TimeIdNeighbors(
                'low5_nn_m', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )

        ## High Abs Related Feature

        feature_list = ['time_id']
        feature_list += top_5_high_abs_feat
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        # df_nn = df_nn.fillna(df_nn.mean())
        
        time_id_neighbors.append(
            TimeIdNeighbors(
                'high5_abs_nn_m', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )

        ## Low Abs Related Feature

        feature_list = ['time_id']
        feature_list += top_5_low_abs_feat
        df_nn = df_pv[feature_list]
        df_nn.set_index('time_id', inplace=True)
        # df_nn = df_nn.fillna(df_nn.mean())

        time_id_neighbors.append(
            TimeIdNeighbors(
                'low5_abs_nn_m', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )


    #### USE ALL FACTOR ####

    if USE_ALL_FEATURES:
        print("ALL FACTORS")

        df_nn = df_pv.copy()
        # df_nn = df_nn.drop(['dv1_realized_volatility'], axis=1)
        df_nn.set_index('time_id', inplace=True)

        # Standard All Feature
        # df_nn[feature_list_for_finding_NN] = scaler.fit_transform(df_nn[feature_list_for_finding_NN])

        df_nn = df_nn[feature_list_for_finding_NN]
        # df_nn = df_nn.fillna(df_nn.mean())

        time_id_neighbors.append(
            TimeIdNeighbors(
                'all_nn_m_p1', 
                df_nn, 
                p=1, 
                exclude_self=True
            )
        )

        # time_id_neighbors.append(
        #     TimeIdNeighbors(
        #         'all_nn_m_p2', 
        #         df_nn, 
        #         p=2, 
        #         exclude_self=True
        #     )
        # )

    #### HAUSDORFF

    if USE_HAUSDORFF_FEATURES:
        print("HAUSDORFF")

        time_id_neighbors.append(
                TimeIdNeighbors('hausdorff', None, p=0, exclude_self=True, haus_metric = True)
        )


ONE FACTOR: Manhattan Distance
name: bidask_spread_1_m_p1, iteration: 0
name: bidask_spread_1_m_p1, iteration: 1000
name: bidask_spread_1_m_p1, iteration: 2000
name: bidask_spread_1_m_p1, iteration: 3000
name: bidask_spread_1_m_p1, iteration: 4000
name: bidask_spread_1_m_p1, iteration: 5000
name: bidask_spread_1_m_p1, iteration: 6000
name: bidask_spread_1_m_p1, iteration: 7000
name: bidask_spread_1_m_p1, iteration: 8000
name: bidask_spread_1_m_p1, iteration: 9000
name: bidask_spread_1_m_p1, iteration: 10000
name: bidask_spread_1_m_p1, iteration: 11000
name: bidask_spread_1_m_p1, iteration: 12000
name: bidask_spread_1_m_p1, iteration: 13000
name: bidask_spread_1_m_p1, iteration: 14000
name: bidask_spread_1_m_p1, iteration: 15000
name: bidask_spread_1_m_p1, iteration: 16000
name: bidask_spread_1_m_p1, iteration: 17000
name: bidask_spread_1_m_p1, iteration: 18000
name: bidask_spread_1_m_p1, iteration: 19000
name: bidask_spread_1_m_p1, iteration: 20000
name: bidask_spread_1_m_p1, iteration

In [ ]:
# time_id_neighbors 변수를 pickle 파일에 저장

import pickle

file_name = "time_id_neighbors.pkl"
with open(file_name, 'wb') as file:
    pickle.dump(time_id_neighbors, file)


In [ ]:
# pickle 파일에서 변수를 불러오기

import pickle

file_name = "time_id_neighbors.pkl"

with open(file_name, 'rb') as file:
    loaded_time_id_neighbors = pickle.load(file)


#### Aggregate Features With NN

In [ ]:
def make_nearest_neighbor_feature(df: pd.DataFrame, data_df: pd.DataFrame) -> pd.DataFrame:
    df2 = df.copy()
    print(df2.shape)

    ### time_id를 기준으로 얻어진 neighbor를 대상으로 feature 만들기

    feature_cols = {}
    for i in range(N_of_features_for_finding_NN):
        feature_cols[feature_list_for_finding_NN[i]] = [np.mean, np.median]


    # feature_cols = {
    #     # 'realized_volatility': [np.mean], #, np.min, np.max, np.std
    #     'realized_volatility_mean0': [np.mean, np.median], # , np.median
    #     # 'realized_volatility_30s': [np.mean, np.median],

    #     # 'dv1_realized_volatility': [np.mean],
    #     'dv2_lowest_return': [np.mean, np.median],
    #     'dv3_highest_return': [np.mean, np.median],
    #     # 'dv4_realized_volatility_30s': [np.mean, np.median],
    #     'dv5_realized_volatility_mean0': [np.mean, np.median],

    #     'num_trades': [np.mean, np.median],
    #     'lowest_return': [np.mean, np.median], # , np.mean, np.min
    #     'highest_return': [np.mean, np.median], # , np.mean, np.min
    #     'high_low_gap': [np.mean, np.median],
    #     'trade_vol': [np.mean, np.median],
    #     # 'volume_power': [np.mean],
    #     'BB_width_w10': [np.mean, np.median],
    #     'BB_width_w20': [np.mean, np.median],
    #     'BB_width_w40': [np.mean, np.median],

    #     'liq_last_1': [np.mean, np.median],
    #     'liq_last_2': [np.mean, np.median],
    #     'liq_last_5': [np.mean, np.median],
    #     'ep_liq_1': [np.mean, np.median],
    #     'ep_liq_2': [np.mean, np.median],
    #     'ep_liq_5': [np.mean, np.median],
    #     'bidask_spread_0': [np.mean, np.median],
    #     'bidask_spread_1': [np.mean, np.median],

    #     'tvpl1': [np.mean, np.median],
    #     'tvpl2': [np.mean, np.median],
    #     'tvpl5': [np.mean, np.median],
    #     'tvpl_ep1': [np.mean, np.median],
    #     'tvpl_ep2': [np.mean, np.median],
    #     'tvpl_ep5': [np.mean, np.median],
    #     'trade.tau': [np.mean, np.median],
    #     'return': [np.mean, np.median],

    # }

    time_id_neigbor_sizes = [1, 2, 4, 8, 16, 32, 64] # 16, 32, 48, 64 메모리 부족으로 계속 오류가 나는 것 같아 이웃 계산 숫자를 줄임.

    ndf: Optional[pd.DataFrame] = None
    
    # 새로운 feature를 기존 df에 추가하는 함수
    def _add_ndf(ndf: Optional[pd.DataFrame], dst: pd.DataFrame) -> pd.DataFrame:
        if ndf is None:
            return dst
        else:
            ndf[dst.columns[-1]] = dst[dst.columns[-1]].astype(np.float32)
            #columns_to_convert = [dst.columns[-1]]  # 열 변환 대상을 선택하거나 여러 열을 지정할 수 있음
            #converted_columns = dst[columns_to_convert].astype(np.float32)
            #ndf = pd.concat([ndf, converted_columns], axis=1)

            return ndf

    # neighbor time_id
    for feature_col in feature_cols.keys():
        gc.collect()
        try: 
            for nn in time_id_neighbors:
                nn.rearrange_feature_values(df2, feature_col, data_df)


            time_id_ns = time_id_neigbor_sizes

            for agg in feature_cols[feature_col]:
                for n in time_id_ns:
                    try:
                        for nn in time_id_neighbors:
                            gc.collect()
                            dst = nn.make_nn_feature(n, agg)
                            ndf = _add_ndf(ndf, dst)
                    except Exception:
                        WHERE_ERROR = feature_col
                        print_trace('time-id nn')
                        pass
        except Exception:
            print_trace('time-id nn')

    if ndf is not None:
        df2 = pd.merge(df2, ndf, on=['time_id'], how='left')
    
    print(df2.shape)
    gc.collect()
    return df2

In [ ]:
# print(type(time_id_neighbors))
print(time_id_neighbors[0].neighbors[:,:10])
print(np.max(time_id_neighbors[0].neighbors[:,:10]))


[[   15    12    17 ...     7    13    14]
 [    6     8    17 ...    12     4    16]
 [   12     8    16 ...    10     6    15]
 ...
 [12897 25289 10688 ... 10136 12795 14858]
 [13551 20860 25512 ... 12272 13079 25443]
 [17312  9187 18255 ... 18318 18551 21845]]
28380


In [ ]:
pd.set_option('display.max_columns', None)

combined_result_df.head(3)

realized_volatility_mean0  num_trades  lowest_return  highest_return  \
0                   0.000105         376      -0.000089        0.001815   
1                   0.000107         361      -0.000089        0.001815   
2                   0.000106         365       0.000000        0.001815   

   high_low_gap  trade_vol              time_id  BB_width_w20  BB_width_w40  \
0      0.001904  13.756273  2022-12-16 21:44:00  48144.957031  47257.070312   
1      0.001904  12.615169  2022-12-16 21:45:00  50564.808594  50311.441406   
2      0.001815  13.313910  2022-12-16 21:46:00  53873.535156  53013.300781   

   BB_width_w10  dv5_realized_volatility_mean0  dv2_lowest_return  \
0  55194.203125                       0.000154          -0.000310   
1  54273.382812                       0.000156          -0.000177   
2  51861.355469                       0.000159          -0.000044   

   dv3_highest_return  realized_volatility_mean0_150  num_trades_150  \
0            0.001238                       0.000046              85   
1            0.001371                       0.000077              68   
2            0.001238                       0.000140              69   

   lowest_return_150  highest_return_150  high_low_gap_150  trade_vol_150  \
0          -0.000089            0.000089          0.000177       3.814411   
1          -0.000089            0.000354          0.000443       1.921894   
2           0.000000            0.000354          0.000354       2.159312   

   realized_volatility_mean0_300  num_trades_300  lowest_return_300  \
0                       0.000100             147          -0.000089   
1                       0.000106             126          -0.000089   
2                       0.000109             125           0.000000   

   highest_return_300  high_low_gap_300  trade_vol_300  \
0            0.000354          0.000443       5.543540   
1            0.000399          0.000487       3.760741   
2            0.000753          0.000753       4.498119   

   realized_volatility_mean0_450  num_trades_450  lowest_return_450  \
0                       0.000092             209          -0.000089   
1                       0.000116             259          -0.000089   
2                       0.000119             286           0.000000   

   highest_return_450  high_low_gap_450  trade_vol_450  liq_last_1  \
0            0.001284          0.001373       9.178568    0.003128   
1            0.001815          0.001904       9.098996    0.001286   
2            0.001815          0.001815       9.661851    0.001621   

   liq_last_2  liq_last_5  liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  \
0    0.003207    0.003479     0.003642     0.003871  0.000475  0.000668   
1    0.001625    0.002044     0.002316     0.002420  0.000472  0.000647   
2    0.001628    0.002304     0.002582     0.002729  0.000489  0.000659   

   ep_liq_5  ep_liq_10  ep_liq_15  bidask_spread_0  bidask_spread_1  \
0  0.001029   0.001296   0.001752         2.030769        10.261539   
1  0.000948   0.001205   0.001527         2.098361        13.000000   
2  0.000952   0.001197   0.001454         1.487500         9.412500   

   liq_last_1_150  liq_last_2_150  liq_last_5_150  liq_last_10_150  \
0        0.001555        0.001703        0.002171         0.002716   
1        0.000299        0.000458        0.000700         0.001334   
2        0.000284        0.001064        0.001406         0.001930   

   liq_last_15_150  ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  \
0         0.003101      0.001283      0.001609      0.002627       0.002997   
1         0.001723      0.000869      0.001128      0.001713       0.002192   
2         0.002127      0.000514      0.000769      0.001105       0.001656   

   ep_liq_15_150  bidask_spread_0_150  bidask_spread_1_150  liq_last_1_300  \
0       0.004168             2.000000             9.000000        0.000238   
1       0.002849             5.636364             9.000000        0.001734   
2       

In [ ]:
combined_result_df_mfl.tail(3)

realized_volatility_mean0  num_trades  lowest_return  highest_return  \
28408                   0.000107        1366       0.000000        0.002821   
28409                   0.000133        1338      -0.000042        0.002316   
28410                   0.000138        1232      -0.000042        0.002273   

       high_low_gap  trade_vol              time_id   BB_width_w20  \
28408      0.002821  67.149895  2023-01-13 18:58:00  109449.148438   
28409      0.002358  69.720497  2023-01-13 18:59:00  107796.296875   
28410      0.002316  69.027657  2023-01-13 19:00:00  105505.500000   

        BB_width_w40  BB_width_w10  dv5_realized_volatility_mean0  \
28408  155788.015625  72738.187500                       0.000132   
28409  153955.531250  63576.375000                       0.000096   
28410  152974.984375  51337.664062                       0.000094   

       dv2_lowest_return  dv3_highest_return  realized_volatility_mean0_150  \
28408          -0.000168            0.002565                       0.000086   
28409          -0.000042            0.002943                       0.000101   
28410           0.000000            0.003614                       0.000145   

       num_trades_150  lowest_return_150  highest_return_150  \
28408             320           0.000000            0.001012   
28409             253          -0.000042            0.000506   
28410             253          -0.000042            0.001011   

       high_low_gap_150  trade_vol_150  realized_volatility_mean0_300  \
28408          0.001012       9.642316                       0.000111   
28409          0.000548       8.778323                       0.000109   
28410          0.001053      10.759177                       0.000109   

       num_trades_300  lowest_return_300  highest_return_300  \
28408             565           0.000000            0.001559   
28409             535          -0.000042            0.001306   
28410             546          -0.000042            0.001979   

       high_low_gap_300  trade_vol_300  realized_volatility_mean0_450  \
28408          0.001559      19.531458                       0.000091   
28409          0.001348      20.565878                       0.000104   
28410          0.002021      23.250544                       0.000115   

       num_trades_450  lowest_return_450  highest_return_450  \
28408            1014           0.000000            0.002695   
28409            1112          -0.000042            0.002316   
28410            1072          -0.000042            0.002273   

       high_low_gap_450  trade_vol_450  liq_last_1  liq_last_2  liq_last_5  \
28408          0.002695      45.652760    0.000062    0.000340    0.001340   
28409          0.002358      57.504150    0.000532    0.000988    0.001084   
28410          0.002316      58.618881    0.001807    0.001866    0.002040   

       liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  ep_liq_5  ep_liq_10  \
28408     0.001699     0.001948  0.000829  0.001150  0.001566   0.001773   
28409     0.001324     0.001614  0.000766  0.001075  0.001484   0.001684   
28410     0.002184     0.002418  0.000764  0.001057  0.001449   0.001648   

       ep_liq_15  bidask_spread_0  bidask_spread_1  liq_last_1_150  \
28408   0.001993         4.095238         8.580953        0.000099   
28409   0.001894         7.591304        13.130435        0.000196   
28410   0.001858         1.571429         8.609524        0.000655   

       liq_last_2_150  liq_last_5_150  liq_last_10_150  liq_last_15_150  \
28408        0.000851        0.001273         0.001337         0.001586   
28409        0.000245        0.001011         0.001196         0.001427   
28410        0.000883        0.002096         0.002362         0.002569   

       ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  ep_liq_15_150  \
28408      0.000823      0.001050      0.001306       0.001499       0.001724   
28409      0.000594      0.000870      0.001175       0.001343       0.001538   
28410      0.00

In [ ]:
gc.collect()

# Cut the first WINDOW_SIZE rows
# input_df = combined_result_df_mfl.drop(index=range(WINDOW_SIZE))
input_df = combined_result_df_mfl.iloc[WINDOW_SIZE:]

with timer('make nearest neighbor feature'):
    df3 = make_nearest_neighbor_feature(input_df, combined_result_df_mfl)

gc.collect()

(8411, 91)


c:\Users\hhkim\AppData\Local\Programs\Python\Python37\lib\site-packages\ipykernel_launcher.py:56: PerformanceWarning: DataFrame is highly fragmented.  This is usually the result of calling `frame.insert` many times, which has poor performance.  Consider joining all columns at once using pd.concat(axis=1) instead.  To get a de-fragmented frame, use `newframe = frame.copy()`


(8411, 9051)
[make nearest neighbor feature]  602.558초


0

In [ ]:
print(df3.shape)
df3.head(3)


(8411, 9051)


realized_volatility_mean0  num_trades  lowest_return  highest_return  \
0                   0.000155         338      -0.001160        0.000186   
1                   0.000177         359      -0.000789        0.000557   
2                   0.000178         363      -0.000789        0.000557   

   high_low_gap  trade_vol              time_id  BB_width_w20  BB_width_w40  \
0      0.001346  12.049068  2023-01-05 15:58:00  20620.888672  27210.669922   
1      0.001346  13.103086  2023-01-05 15:59:00  19948.353516  23676.451172   
2      0.001346  12.706044  2023-01-05 16:00:00  19095.328125  20188.851562   

   BB_width_w10  dv5_realized_volatility_mean0  dv2_lowest_return  \
0  22881.335938                       0.000191          -0.001207   
1  23232.162109                       0.000160          -0.001207   
2  22799.609375                       0.000159          -0.001114   

   dv3_highest_return  realized_volatility_mean0_150  num_trades_150  \
0            0.000232                       0.000114              44   
1            0.000000                       0.000045              54   
2            0.000139                       0.000042              57   

   lowest_return_150  highest_return_150  high_low_gap_150  trade_vol_150  \
0          -0.000464            0.000000          0.000464       1.894086   
1          -0.000186            0.000046          0.000232       2.382331   
2          -0.000232            0.000000          0.000232       2.608287   

   realized_volatility_mean0_300  num_trades_300  lowest_return_300  \
0                       0.000077             119          -0.000603   
1                       0.000075             143          -0.000325   
2                       0.000188             195          -0.000789   

   highest_return_300  high_low_gap_300  trade_vol_300  \
0            0.000000          0.000603       4.710686   
1            0.000232          0.000557       6.082892   
2            0.000371          0.001160       8.167232   

   realized_volatility_mean0_450  num_trades_450  lowest_return_450  \
0                       0.000174             248          -0.001160   
1                       0.000161             277          -0.000789   
2                       0.000157             296          -0.000789   

   highest_return_450  high_low_gap_450  trade_vol_450  liq_last_1  \
0            0.000186          0.001346       9.954347    0.000105   
1            0.000557          0.001346      10.510321    0.000224   
2            0.000557          0.001346      10.489419    0.000375   

   liq_last_2  liq_last_5  liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  \
0    0.000217    0.000476     0.000696     0.000837  0.000424  0.000537   
1    0.000399    0.000656     0.000909     0.001050  0.000350  0.000463   
2    0.000808    0.001140     0.001438     0.001531  0.000346  0.000469   

   ep_liq_5  ep_liq_10  ep_liq_15  bidask_spread_0  bidask_spread_1  \
0  0.000810   0.001057   0.001180         7.366460        13.832298   
1  0.000722   0.000962   0.001094        11.097345        24.778761   
2  0.000731   0.000968   0.001098         3.895833        13.635417   

   liq_last_1_150  liq_last_2_150  liq_last_5_150  liq_last_10_150  \
0        0.001113        0.001132        0.001422         0.001878   
1        0.001081        0.001097        0.001279         0.001598   
2        0.000346        0.000871        0.001061         0.001390   

   liq_last_15_150  ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  \
0         0.002048      0.000524      0.000674      0.000999       0.001334   
1         0.001868      0.000588      0.000739      0.001014       0.001419   
2         0.001598      0.000529      0.000768      0.001011       0.001411   

   ep_liq_15_150  bidask_spread_0_150  bidask_spread_1_150  liq_last_1_300  \
0       0.001504             2.000000             5.318182        0.000140   
1       0.001632             1.142857             3.964286        0.000055   
2       

In [ ]:
df3.to_csv(working_directory + "output\\temp_1105_second_after_30000.csv", index=False)

In [27]:
import pandas as pd

# Create two sample dataframes
temp1 = pd.read_csv(working_directory +"output\\BTC_sum_plus_nn_features_for_dv5.csv")
temp2 = df3

print(temp1.shape)
print(temp2.shape)



(64619, 2695)
(2202, 2695)


In [28]:
# Concatenate them as new rows
result = pd.concat([temp1, temp2], ignore_index=True)

In [29]:
result.shape

(66821, 2695)

In [30]:
result.drop_duplicates(subset = 'time_id',keep='first', inplace=True)


In [31]:
result.shape

(65030, 2695)

In [160]:
temp1.tail(3)

realized_volatility_mean0  num_trades  lowest_return  highest_return  \
8879                   0.000203         365      -0.001948        0.000093   
8880                   0.000185         467      -0.002598        0.000139   
8881                   0.000175         549      -0.002830        0.000046   

      high_low_gap  trade_vol              time_id  BB_width_w20  \
8879      0.002040  19.208967  2023-01-04 13:57:00     41969.914   
8880      0.002737  25.359545  2023-01-04 13:58:00     50702.848   
8881      0.002876  29.646381  2023-01-04 13:59:00     62690.215   

      BB_width_w40  BB_width_w10  dv5_realized_volatility_mean0  \
8879     40503.370     47232.758                       0.000169   
8880     47045.970     59723.810                       0.000186   
8881     56604.703     73453.234                       0.000202   

      dv2_lowest_return  dv3_highest_return  realized_volatility_mean0_150  \
8879          -0.001207            0.000603                       0.000059   
8880          -0.000790            0.001021                       0.000098   
8881          -0.000279            0.001532                       0.000305   

      num_trades_150  lowest_return_150  highest_return_150  high_low_gap_150  \
8879              75          -0.000278            0.000093          0.000371   
8880              87          -0.000232            0.000139          0.000371   
8881             103          -0.000927            0.000046          0.000973   

      trade_vol_150  realized_volatility_mean0_300  num_trades_300  \
8879       2.666636                       0.000253             160   
8880       3.258465                       0.000276             147   
8881       4.380208                       0.000286             147   

      lowest_return_300  highest_return_300  high_low_gap_300  trade_vol_300  \
8879          -0.001020            0.000093          0.001112       6.548009   
8880          -0.000973            0.000139          0.001112       6.101820   
8881          -0.000927            0.000046          0.000973       5.625350   

      realized_volatility_mean0_450  num_trades_450  lowest_return_450  \
8879                       0.000239             221          -0.001020   
8880                       0.000223             256          -0.001159   
8881                       0.000228             285          -0.001716   

      highest_return_450  high_low_gap_450  trade_vol_450  liq_last_1  \
8879            0.000093          0.001112       8.841516    0.000390   
8880            0.000139          0.001298      12.222675    0.000322   
8881            0.000046          0.001762      13.674121    0.000006   

      liq_last_2  liq_last_5  liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  \
8879    0.000408    0.000661     0.001011     0.001197  0.000293  0.000428   
8880    0.000497    0.000602     0.000979     0.001133  0.000310  0.000449   
8881    0.001181    0.001599     0.001789     0.001959  0.000337  0.000488   

      ep_liq_5  ep_liq_10  ep_liq_15  bidask_spread_0  bidask_spread_1  \
8879  0.000759   0.001049   0.001283         4.487395        10.563025   
8880  0.000766   0.001064   0.001271         1.511811         9.118111   
8881  0.000811   0.001099   0.001288         2.071429        12.335714   

      liq_last_1_150  liq_last_2_150  liq_last_5_150  liq_last_10_150  \
8879        0.000131        0.000555        0.000749         0.001133   
8880        0.000057        0.000798        0.001016         0.001438   
8881        0.000009        0.000364        0.000813         0.001012   

      liq_last_15_150  ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  \
8879         0.001613      0.000703      0.000841      0.001093   
8880         0.001831      0.000473      0.000590      0.000792   
8881         0.001163      0.000141      0.000259      0.000528   

      ep_liq_10_150  ep_liq_15_150  bidask_spread_0_150  bidask_spread_1_150  \
8879       0.001449       0.001880             2.689655             6

In [161]:
temp2.head(3)

realized_volatility_mean0  num_trades  lowest_return  highest_return  \
0                   0.000054         333      -0.000139        0.000417   
1                   0.000060         364      -0.000650        0.000417   
2                   0.000069         408      -0.000882        0.000557   

   high_low_gap  trade_vol              time_id  BB_width_w20  BB_width_w40  \
0      0.000557  20.134951  2023-01-04 21:11:00  27452.542969  42367.742188   
1      0.001067  20.520779  2023-01-04 21:12:00  23123.466797  42399.683594   
2      0.001439  20.930735  2023-01-04 21:13:00  27206.037109  42106.582031   

   BB_width_w10  dv5_realized_volatility_mean0  dv2_lowest_return  \
0  12103.259766                       0.000196          -0.001160   
1  23232.162109                       0.000199          -0.000371   
2  35537.773438                       0.000198          -0.000046   

   dv3_highest_return  realized_volatility_mean0_150  num_trades_150  \
0            0.000000                       0.000086              46   
1            0.000789                       0.000064              77   
2            0.001114                       0.000050              94   

   lowest_return_150  highest_return_150  high_low_gap_150  trade_vol_150  \
0          -0.000139            0.000139          0.000278       2.964197   
1          -0.000139            0.000139          0.000278       3.076633   
2           0.000000            0.000278          0.000278       3.414210   

   realized_volatility_mean0_300  num_trades_300  lowest_return_300  \
0                       0.000060             135          -0.000139   
1                       0.000050             141          -0.000139   
2                       0.000041             168           0.000000   

   highest_return_300  high_low_gap_300  trade_vol_300  \
0            0.000139          0.000278       6.098859   
1            0.000139          0.000278       6.929142   
2            0.000418          0.000418       7.025306   

   realized_volatility_mean0_450  num_trades_450  lowest_return_450  \
0                       0.000052             217          -0.000139   
1                       0.000048             239          -0.000139   
2                       0.000047             284           0.000000   

   highest_return_450  high_low_gap_450  trade_vol_450  liq_last_1  \
0            0.000278          0.000418      10.999846    0.001048   
1            0.000417          0.000557      11.801092    0.000303   
2            0.000557          0.000557      12.149213    0.004901   

   liq_last_2  liq_last_5  liq_last_10  liq_last_15  ep_liq_1  ep_liq_2  \
0    0.001121    0.001340     0.001443     0.002005  0.000964  0.001640   
1    0.000462    0.000920     0.001274     0.001467  0.000802  0.001418   
2    0.004906    0.005232     0.005565     0.005948  0.000691  0.001204   

   ep_liq_5  ep_liq_10  ep_liq_15  bidask_spread_0  bidask_spread_1  \
0  0.002220   0.002651   0.003337         2.300000         5.200000   
1  0.001975   0.002391   0.002976         3.486486         7.175676   
2  0.001669   0.002019   0.002451         3.649485         8.036082   

   liq_last_1_150  liq_last_2_150  liq_last_5_150  liq_last_10_150  \
0        0.000223        0.000361        0.000499         0.000767   
1        0.000345        0.000455        0.000616         0.000980   
2        0.007331        0.009770        0.009912         0.010154   

   liq_last_15_150  ep_liq_1_150  ep_liq_2_150  ep_liq_5_150  ep_liq_10_150  \
0         0.001843      0.000626      0.000816      0.000964       0.001351   
1         0.001555      0.000440      0.000588      0.000726       0.001122   
2         0.010986      0.000867      0.001298      0.001567       0.001940   

   ep_liq_15_150  bidask_spread_0_150  bidask_spread_1_150  liq_last_1_300  \
0       0.002238             3.000000             7.818182        0.006807   
1       0.001835             2.631579             7.947369        0.000152   
2       

In [ ]:
# Cut the first 'window_size' (15,000 or something) rows. <= These rows do not have appropriate nearest neighbors.
# WINDOW_SIZE=20000
# df3 = df3.drop(index=range(WINDOW_SIZE))

coin = 'BTC'
result.to_csv(working_directory + "output\\{}_sum_plus_nn_features_for_{}_{}.csv".format(coin, target_var_3, vn), index=False)

## NN 추출끼리 비슷한가 아니면 다른가?

In [ ]:
def calculate_rank_correraltion(neighbors, top_n=10):
    if not neighbors:
        return
    neighbor_indices = pd.DataFrame()
    for n in neighbors:
        neighbor_indices[n.name] = n.neighbors[:,:top_n].flatten()
        display(neighbor_indices[n.name])
    sns.heatmap(neighbor_indices.corr('kendall'), annot=True)
    

In [ ]:
time_ids = np.array(sorted(df3['time_id'].unique()))
for neighbor in time_id_neighbors:
    print(neighbor)
    display(
        pd.DataFrame(
            time_ids[neighbor.neighbors[:,:10]], 
            index=pd.Index(time_ids, name='time_id'), 
            columns=[f'top_{i+1}' for i in range(10)]
        ).iloc[1:6]
    )
    print(pd.DataFrame(
            time_ids[neighbor.neighbors[:,:10]], 
            index=pd.Index(time_ids, name='time_id'), 
            columns=[f'top_{i+1}' for i in range(10)]
        ).shape)

In [ ]:
calculate_rank_correraltion(time_id_neighbors)

In [ ]:
# # TEMP code

# import gc
# import pandas as pd
# import os
# os.environ["MODIN_ENGINE"] = "dask"  # Modin will use Dask
# working_directory = 'D:\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'  ## 서로 다른 환경에서는 이곳을 수정해야 함.
# # working_directory = 'C:\\Users\\user\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'

# os.chdir(working_directory)
# gc.collect()

# # combined_result_df = pd.read_csv("./DB/professor_BTC_sum_both_10m.csv")
# coin = 'BTC'
# target_var = 'dv5_realized_volatility_mean0'
# target_var_3 = target_var[:3]
# df3 = pd.read_csv("./output/{}_sum_plus_nn_features_for_{}.csv".format(coin, target_var_3))

# window_size=10000
# df3 = df3.drop(index=range(window_size))
# df3.to_csv(working_directory + "output\\{}_sum_plus_nn_features_for_{}.csv".format(coin, target_var_3), index=False)


### Checking the final outcome

In [ ]:
import gc
import pandas as pd
import os
os.environ["MODIN_ENGINE"] = "dask"  # Modin will use Dask
working_directory = 'D:\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'  ## 서로 다른 환경에서는 이곳을 수정해야 함.
# working_directory = 'C:\\Users\\user\\OneDrive - 한동대학교\\PROJECT\\트머프로젝트\\'

os.chdir(working_directory)
gc.collect()

# combined_result_df = pd.read_csv("./DB/professor_BTC_sum_both_10m.csv")
coin = 'BTC'
target_var = 'dv5_realized_volatility_mean0'
target_var_3 = target_var[:3]
df3 = pd.read_csv("./output/{}_sum_plus_nn_features_for_{}.csv".format(coin, target_var_3))

df3.head(3)
print("# of rows:", df3.shape[0])
print("# of columns:", df3.shape[1])

In [ ]:
df3.columns